In [2]:
!pip install selenium

In [1]:
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions
from selenium.common.exceptions import NoSuchElementException

from difflib import SequenceMatcher
from bs4 import BeautifulSoup
############################################################
import os, csv
import time


class search_save_CSV:
    def __init__(self, i=0):
        
        header = [\
            "user-agent=Mozilla/5.0 (Windows NT 6.1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/41.0.2228.0 Safari/537.3", \
            "user-agent=Mozilla/5.0 (Windows NT 6.3; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/63.0.3239.132 Safari/537.36", \
            "user-agent=Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_5) AppleWebKit 537.36 (KHTML, like Gecko) Chrome", \
        ]
        
        options = webdriver.ChromeOptions()
        # options.add_argument('headless')
        options.add_argument('--no-sandbox')
        options.add_argument('--disable-dev-shm-usage')
        options.add_argument(header[i])
        options.add_argument('Accept-Charset=utf-8')
        
        self.driver = webdriver.Chrome("./chromedriver.exe", options=options)
        self.driver.implicitly_wait(5)
        
    def getKeyword_andOpen(self, search_text):
        self.driver.get("https://m.map.naver.com/")
        
        self.search_ = search_text
        self.driver.find_element_by_class_name("Nsearch._searchKeywordView._searchGuide").click()
        
        self.driver.find_element_by_class_name("Nbox_input_text._search_input").send_keys(self.search_)
        self.driver.find_element_by_class_name("_formSearch").submit()
        
    def errorCheck(self):
        # print(self.driver.find_element_by_class_name('interstitial-wrapper'))
        try:
            self.driver.find_element_by_class_name('interstitial-wrapper')
            print("error-reload")
            return True
        except NoSuchElementException:
            return False
        
    def search_and_save(self):
        searchList = self.driver.find_elements_by_class_name("_item._lazyImgContainer")
        choicePer, choiceIndex = 0, -1
        for i, element in enumerate(searchList):
            # print(i, ":", element.get_attribute("data-title"))    
            ratio = self.getMatchPercent(element.get_attribute("data-title"), self.search_)
            print("{0:.1f}%".format(ratio))
            
            if ratio < 50:
                pass
            else:
                if choicePer < ratio:
                    choicePer = ratio
                    choiceIndex = i
        if choiceIndex == -1:
            print("일치결과 없음")
            return False
        else:
            print("선택 index {0} : {1} 과의 일치율 {2:.1f}".format(choiceIndex, self.search_, choicePer))
            self.index = choiceIndex
            return True
        
    def get_menu_list(self): 
        elements = self.driver.find_elements_by_class_name("sp_map.btn_price._linkMenu")
        try:
            elements[self.index].click()
        except Exception:
            "가격정보 없음"
            return False
        time.sleep(5)
        
        temp = str(self.driver.current_url)
        temp = temp[:-4] + 'menu/list'
        print(temp)
        self.driver.get(temp)
        
        soup = BeautifulSoup(self.driver.page_source, 'html.parser')
        elements = soup.find_all("li", class_="_1jXsR")
        menuName = soup.find_all("span", class_="_1zr5s")
        menuPrice = soup.find_all("div", class_="_1cQ4a")

        for i, menu in enumerate(menuName):
            print(i, menu.text, ":", menuPrice[i].text)
        self.name = menuName
        self.price = menuPrice
        return True
        
    def save_to_csv(self, pk):
        saveFileName = os.path.abspath("../data/price.csv")
        if not os.path.exists(saveFileName):
            file = open(saveFileName, "w", newline="", encoding='utf-8')
            newWriter = csv.writer(file)
            newWriter.writerow(["관리번호", "메뉴이름", "가격"])
            file.close()
        file = open(saveFileName, "a", newline="", encoding='utf-8')
        writer = csv.writer(file)
        for i, menu in enumerate(self.name):
            row = [str(pk), menu.text, self.price[i].text]
            writer.writerow(row)
        file.close()      
        
        
    def getMatchPercent(self, one, two):
        s = SequenceMatcher(None, one, two)
        return s.ratio() * 100
    
    def close_driver(self):
        self.driver.quit()

In [2]:
from pyspark import SparkContext, SparkConf

conf = SparkConf().setAppName("coffee-price").setMaster("local[*]")
sc = SparkContext(conf=conf).getOrCreate()

In [3]:
import os

data_path = os.path.join("..", "data", "data.csv")
raw_data = sc.textFile(data_path)
raw_data_header = raw_data.take(1)[0]

In [4]:
headerList = str(raw_data_header).split(",") # 관리번호 = PK
need_column = ['관리번호', '영업상태구분코드', '영업상태명', '소재지전화',\
        '소재지면적','소재지전체주소', '도로명전체주소', '사업장명', '최종수정시점',\
        '업태구분명', '좌표정보(X)', '좌표정보(Y)', '시설총규모', '홈페이지']
need_column_index = []
column_list = []
for i, value in enumerate(headerList):
    if str(value) in need_column:
        need_column_index.append(i)
        column_list.append(str(value))

In [5]:
data = raw_data.filter(lambda line: line!=raw_data_header) \
    .map(lambda line: line.split(",")) \
    .filter(lambda tokens: tokens[24] == '커피숍' and tokens[7] =='영업/정상') \
    .map(lambda tokens: [tokens[i] for i in need_column_index])

In [7]:
elements = data.take(100000)
dongList = list()
num = 0
search = search_save_CSV(num)

for i, element in enumerate(elements):
    print(i, "번째.")
    if i%10 == 9:
        search.close_driver()
        time.sleep(1)
        num = num + 1
        search = search_save_CSV(num % 3)
    for i in range(len(column_list)):
        print("[%s]" % i, column_list[i], ":", element[i])
    continue_list = \
    ["스타벅스", "이디야", "투썸", "투썸플레이스", "엔젤리너스", "커피빈", "구스토", "달콤커피", "메가커피", \
    "바나프레소", "빽다방", "셀렉토", "요거프레소", "주커피", "드롭탑", "띠아모", "카페베네", "봄봄", \
    "커핀그루나루", "커피마마", "커피에 반하다", "탐앤탐스", "폴 바셋", "할리스", "파스쿠찌", "쥬씨"]
    
    name_list = str(element[7]).split()
    flag = False
    for comp in name_list:
        for li in continue_list:
            if li in comp:
                flag = True
                break
        if flag:
            break
    if flag: # 프랜차이즈의 경우는 넘어간다.
        continue
    
    address = str(element[5]).split()
    try:
        dongList.append(address[2])
        print("************************************************")
        search_keyword = address[2] + " " + element[7]
        
        search.getKeyword_andOpen(search_keyword)
    
        
        # check error page
        while search.errorCheck():
            time.sleep(10)
#             search.close_driver()
#             num = num + 1
#             search = search_save_CSV(num % 3)
            search.getKeyword_andOpen(search_keyword)
            
            
        flag_ = search.search_and_save()
        if flag_:
            if search.get_menu_list():
                time.sleep(1)
                search.save_to_csv(element[0])
    except Exception:
        continue
search.close_driver()

0 번째.
[0] 관리번호 : 3000000-104-2007-00069
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : None
[5] 소재지전체주소 : 서울특별시 종로구 도렴동 83번지
[6] 도로명전체주소 : None
[7] 사업장명 : 세븐일레븐(S광화문역점)
[8] 최종수정시점 : 20140423140411
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : None
[11] 좌표정보(Y) : None
[12] 시설총규모 : 6.6
[13] 홈페이지 : None
************************************************
75.9%
선택 index 0 : 도렴동 세븐일레븐(S광화문역점) 과의 일치율 75.9
1 번째.
[0] 관리번호 : 3000000-104-2018-00110
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 000234469383
[4] 소재지면적 : None
[5] 소재지전체주소 : 서울특별시 종로구 혜화동 179-4번지
[6] 도로명전체주소 : 서울특별시 종로구 동숭길 148 (혜화동)
[7] 사업장명 : 커피스미스 대학로 서경대점
[8] 최종수정시점 : 20180806151218
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 200121.775059748
[11] 좌표정보(Y) : 453468.191493695
[12] 시설총규모 : 173.58
[13] 홈페이지 : None
************************************************
87.5%
선택 index 0 : 혜화동 커피스미스 대학로 서경대점 과의 일치율 87.5
https://m.place.naver.com/restaurant/1623447444/menu/list
0 에스프레소 : 4,000원
1 에스프레소 마끼아또 : 4,300원
2 카페 아메리카노 : 4,500원
3 카페라떼 : 5,000원
4 

26.7%
36.4%
44.4%
30.8%
36.4%
36.4%
13.3%
일치결과 없음
18 번째.
[0] 관리번호 : 3000000-104-2010-00005
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 02 7588316
[4] 소재지면적 : 342.53
[5] 소재지전체주소 : 서울특별시 종로구 명륜4가 7번지
[6] 도로명전체주소 : 서울특별시 종로구 대명길 5 (명륜4가)
[7] 사업장명 : 스타벅스 대명거리점
[8] 최종수정시점 : 20190522101658
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 200032.052063871
[11] 좌표정보(Y) : 453467.12206246
[12] 시설총규모 : 342.53
[13] 홈페이지 : None
19 번째.
[0] 관리번호 : 3000000-104-2010-00007
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 07075841223
[4] 소재지면적 : None
[5] 소재지전체주소 : 서울특별시 종로구 신영동 100-2번지
[6] 도로명전체주소 : 서울특별시 종로구 세검정로6나길 1 (신영동)
[7] 사업장명 : 올 소울스
[8] 최종수정시점 : 20120316140620
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 196614.275863481
[11] 좌표정보(Y) : 455417.425440214
[12] 시설총규모 : 26.4
[13] 홈페이지 : None
************************************************
일치결과 없음
20 번째.
[0] 관리번호 : 3000000-104-2009-00029
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 000207424300
[4] 소재지면적 : None
[5] 소재지전체주소 : 서울특별시 종로구 연건동 138-2번지
[6] 도로명전체주소 : 서울특별시 종로구 대학로 7

https://m.place.naver.com/restaurant/1405105046/menu/list
0 이지그린 : 4,900원
1 이지레드 : 4,900원
2 비타오제이 : 4,900원
3 클렌즈하프 : 26,000원
36 번째.
[0] 관리번호 : 3000000-104-2013-00018
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 02  741 5056
[4] 소재지면적 : None
[5] 소재지전체주소 : 서울특별시 종로구 운니동 16번지
[6] 도로명전체주소 : 서울특별시 종로구 율곡로6길 15 (운니동)
[7] 사업장명 : 씨유 종로창덕궁점
[8] 최종수정시점 : 20130227132742
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 198993.740420535
[11] 좌표정보(Y) : 452697.981100444
[12] 시설총규모 : 3.3
[13] 홈페이지 : None
************************************************
63.6%
선택 index 0 : 운니동 씨유 종로창덕궁점 과의 일치율 63.6
37 번째.
[0] 관리번호 : 3000000-104-2013-00019
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 02  64028328
[4] 소재지면적 : None
[5] 소재지전체주소 : 서울특별시 종로구 세종로 1-68번지
[6] 도로명전체주소 : 서울특별시 종로구 세종대로 지하 172 (세종로)
[7] 사업장명 : 큐비드
[8] 최종수정시점 : 20130227145518
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 197889.89798215
[11] 좌표정보(Y) : 452238.323737682
[12] 시설총규모 : 6.6
[13] 홈페이지 : None
************************************************
일치결과 없음
38 번째.
[0] 관리번호 : 

0 하양두유/깜장두유 : 변동
54 번째.
[0] 관리번호 : 3000000-104-2018-00038
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : None
[5] 소재지전체주소 : 서울특별시 종로구 교남동 62-1번지 팰리스에비뉴4BL 4123호
[6] 도로명전체주소 : None
[7] 사업장명 : GS25 경희궁자이점
[8] 최종수정시점 : 20180308110210
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 196732.952434799
[11] 좌표정보(Y) : 451863.826336965
[12] 시설총규모 : 6
[13] 홈페이지 : None
************************************************
84.6%
선택 index 0 : 교남동 GS25 경희궁자이점 과의 일치율 84.6
55 번째.
[0] 관리번호 : 3000000-104-2018-00044
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : None
[5] 소재지전체주소 : 서울특별시 종로구 교남동 62-1번지 3BL동 3114호
[6] 도로명전체주소 : None
[7] 사업장명 : 커피공장103광화문점
[8] 최종수정시점 : 20180313133554
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 196732.952434799
[11] 좌표정보(Y) : 451863.826336965
[12] 시설총규모 : 35.3
[13] 홈페이지 : None
************************************************
81.5%
선택 index 0 : 교남동 커피공장103광화문점 과의 일치율 81.5
https://m.place.naver.com/restaurant/1036586883/menu/list
0 아메리카노 Hot : 2,500원
1 [드립커피] 이디오피아 블랜드 : 3,500

일치결과 없음
71 번째.
[0] 관리번호 : 3010000-104-2007-00088
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 02 7777484
[4] 소재지면적 : 63.00
[5] 소재지전체주소 : 서울특별시 중구 다동 164-1번지
[6] 도로명전체주소 : 서울특별시 중구 다동길 24-8 (다동)
[7] 사업장명 : 다동커피집
[8] 최종수정시점 : 20090515174115
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 198212.655427223
[11] 좌표정보(Y) : 451688.098895051
[12] 시설총규모 : 63
[13] 홈페이지 : None
************************************************
76.9%
선택 index 0 : 다동 다동커피집 과의 일치율 76.9
https://m.place.naver.com/restaurant/19862051/menu/list
0 입장료 : 4,500원
72 번째.
[0] 관리번호 : 3010000-104-2002-00170
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : 17.00
[5] 소재지전체주소 : 서울특별시 중구 장충동2가 189-2번지 (동대입구역322-13)
[6] 도로명전체주소 : None
[7] 사업장명 : 클럽알앤비
[8] 최종수정시점 : 20021105000000
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : None
[11] 좌표정보(Y) : None
[12] 시설총규모 : 17
[13] 홈페이지 : None
************************************************
일치결과 없음
73 번째.
[0] 관리번호 : 3010000-104-2019-00276
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : 17.36


...

75.0%
선택 index 0 : 도천면 카페in도천 과의 일치율 75.0
https://m.place.naver.com/restaurant/1983117885/menu/list
0 아메리카노 : 3,000원
8619 번째.
[0] 관리번호 : 5420000-104-2019-00001
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : 20.40
[5] 소재지전체주소 : 경상남도 고성군 회화면 배둔리 494-8번지
[6] 도로명전체주소 : 경상남도 고성군 회화면 관인로 10
[7] 사업장명 : 빈애
[8] 최종수정시점 : 20190305174159
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 324970.347012437
[11] 좌표정보(Y) : 173861.60678091
[12] 시설총규모 : 20.4
[13] 홈페이지 : None
************************************************
50.0%
선택 index 0 : 회화면 빈애 과의 일치율 50.0
https://m.place.naver.com/restaurant/1146346885/menu/list
0 아메리카노 : 3,000원
1 더치커피 250ml : 6,000원
2 더치커피 500ml : 11,000원
3 디카페인 더치커피 250ml : 8,000원
4 디카페인 더치커피 500ml : 15,000원
5 원두 100gm : 5,000원
6 원두 200gm : 9,000원
7 핸드드립커피 : 4,500원
8 콜드브루 : 4,000원
9 디카페인 콜드브루 : 4,500원
10 아인슈페너 : 4,000원
11 와플 : 4,500원
12 와플+아이스크림 : 6,000원
8620 번째.
[0] 관리번호 : 5420000-104-2019-00002
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : 27.72
[5] 소재지전체주소 : 경

0 커피 : 3,000원
1 수제대추차 : 4,500원
2 수제차 : 5,000원
8636 번째.
[0] 관리번호 : 5420000-104-2015-00011
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 055 672 1989
[4] 소재지면적 : 40.32
[5] 소재지전체주소 : 경상남도 고성군 거류면 당동리 120-4번지
[6] 도로명전체주소 : 경상남도 고성군 거류면 거류로 670
[7] 사업장명 : 당동박씨네커피
[8] 최종수정시점 : 20150817141347
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 328219.577869208
[11] 좌표정보(Y) : 166662.496381327
[12] 시설총규모 : 40.32
[13] 홈페이지 : None
************************************************
77.8%
선택 index 0 : 거류면 당동박씨네커피 과의 일치율 77.8
https://m.place.naver.com/restaurant/37060799/menu/list
0 쏠티카라멜크림커피 : 5,000원
1 수제치즈케이크 : 4,500원
2 수제마카롱 : 2,000원
3 블루베리요거트스무디 : 5,500원
4 죠리퐁스무디 : 4,500원
8637 번째.
[0] 관리번호 : 5420000-104-2016-00003
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : 005506744700
[4] 소재지면적 : 109.12
[5] 소재지전체주소 : 경상남도 고성군 고성읍 동외리 312-3번지
[6] 도로명전체주소 : 경상남도 고성군 고성읍 동외로 137
[7] 사업장명 : 이디야
[8] 최종수정시점 : 20171120155819
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 320981.354510697
[11] 좌표정보(Y) : 164651.315127325
[12] 시설총규모 : 109.12
[13] 홈페이지 

일치결과 없음
8655 번째.
[0] 관리번호 : 5430000-104-2019-00001
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : 30.00
[5] 소재지전체주소 : 경상남도 남해군 남해읍 아산리 1270-7번지
[6] 도로명전체주소 : 경상남도 남해군 남해읍 오동로 118
[7] 사업장명 : 지튼
[8] 최종수정시점 : 20190111153559
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 280744.625569583
[11] 좌표정보(Y) : 150294.864568496
[12] 시설총규모 : 30
[13] 홈페이지 : None
************************************************
36.4%
일치결과 없음
8656 번째.
[0] 관리번호 : 5430000-104-2019-00003
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : 22.50
[5] 소재지전체주소 : 경상남도 남해군 삼동면 동천리 994-2번지 (2층)
[6] 도로명전체주소 : 경상남도 남해군 삼동면 동부대로 1254 (2층)
[7] 사업장명 : 블랙스완커피(BLACSWAN COFFEE)
[8] 최종수정시점 : 20190211132113
[9] 업태구분명 : 커피숍
[10] 좌표정보(X) : 294943.373413112
[11] 좌표정보(Y) : 145797.598727853
[12] 시설총규모 : 22.5
[13] 홈페이지 : None
************************************************
일치결과 없음
8657 번째.
[0] 관리번호 : 5430000-104-2019-00005
[1] 영업상태구분코드 : 01
[2] 영업상태명 : 영업/정상
[3] 소재지전화 : None
[4] 소재지면적 : 91.20
[5] 소재지전체주소 : 경상남도 남해군 미조면 미조리 104-8

error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload
error-reload


KeyboardInterrupt: 